# CS109A Project Group 21
# Baseline Model

*****

In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import NearestNeighbors
from scipy.sparse import csr_matrix
from collections import Counter

### Importing the relevant datasets

First we import two subset of 100 playlists, each subset of 100 playlists to be used for the training and test sets respectively. 

These playlists are randomly chosen from the full one million playlist dataset that has been matched with the Spotify API data, thus including data on track-specific features such as loudness, speechiness and tempo.

In [2]:
train_df = pd.read_csv("data/subset100playlists.csv")
test_df = pd.read_csv("data/subset100playlists_test.csv")

In [3]:
train_df.head()

Unnamed: 0  index   pid  pos                             track_uri  \
0           0    107  6011    0  spotify:track:2FBUoWkIuQXwayw2RNo5l6   
1           1    107  6011    1  spotify:track:25khomWgBVamSdKw7hzm3l   
2           2    107  6011    2  spotify:track:2NVt7fxr5GsqTkGwYXcNTE   
3           3    107  6011    3  spotify:track:5NQbUaeTEOGdD6hHcre0dZ   
4           4    107  6011    4  spotify:track:5hJFhO9dvhJoDvUZZ9iWSw   

                            artist_uri_x             track_name  \
0  spotify:artist:3TVXtAsR1Inumwj472S9r4          Hotline Bling   
1  spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ              The Hills   
2  spotify:artist:5lHRUCqkQZCIWeX7xG4sYT   Flex (Ooh, Ooh, Ooh)   
3  spotify:artist:6PXS4YHDkKvl1wkIl4V8DL  679 (feat. Remy Boyz)   
4  spotify:artist:360IAlyVv4PCEVjgyMZrxK                  Adorn   

       artist_name                           artist_uri_y  \
0            Drake  spotify:artist:3TVXtAsR1Inumwj472S9r4   
1       The Weeknd  spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ   
2  Rich Homie Quan  spotify:artist:5lHRUCqkQZCIWeX7xG4sYT   
3        Fetty Wap  spotify:artist:6PXS4YHDkKvl1wkIl4V8DL   
4           Miguel  spotify:artist:360IAlyVv4PCEVjgyMZrxK   

                            album_name  ... key  liveness  loudness mode  \
0                                Views  ...   2    0.0504    -8.094    1   
1            Beauty Behind The Madness  ...   0    0.1370    -7.011    0   
2                 Flex (Ooh, Ooh, Ooh)  ...   6    0.3410    -7.534    0   
3                679 (feat. Remy Boyz)  ...   7    0.6250    -5.738    1   
4  Kaleidoscope Dream (Deluxe Version)  ...  11    0.1870    -5.693    0   

   speechiness    tempo  time_signature  \
0       0.0587  134.960               4   
1       0.0798  135.553               5   
2       0.0496  163.993               4   
3       0.3180  190.050               4   
4       0.1750  179.063               4   

                                          track_href            type  valence  
0  https://api.spotify.com/v1/tracks/2FBUoWkIuQXw...  audio_features    0.539  
1  https://api.spotify.com/v1/tracks/25khomWgBVam...  audio_features    0.109  
2  https://api.spotify.com/v1/tracks/2NVt7fxr5Gsq...  audio_features    0.883  
3  https://api.spotify.com/v1/tracks/5NQbUaeTEOGd...  audio_features    0.603  
4  https://api.spotify.com/v1/tracks/5hJFhO9dvhJo...  audio_features    0.235  

[5 rows x 29 columns]

### Creating the train and test set

We then create the train and test set by keeping select numeric features and the track URI, as a way to maintain a unique ID for each song.

Specifically, for the test set, we split it into two subsets: calibration (20%) and withheld songs (80%), where the calibration songs are used as inputs to the model to predict songs. These predicted songs are then compared to the withheld songs, using R precision score as a comparison metric.

In [4]:
numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
df_cleaned= train_df.select_dtypes(include=numerics)

var_drop = ["index","pid","pos", "count", "Unnamed: 0"]
df_cleaned = df_cleaned.drop(var_drop, axis =1)

train = pd.concat([df_cleaned, train_df['track_uri']],axis=1)

In [5]:
test_df_cleaned = test_df.select_dtypes(include=numerics)

test_var_drop = ["index","pos", "count", "Unnamed: 0"]
test_df_cleaned = test_df_cleaned.drop(test_var_drop, axis =1)

test_df_cleaned = pd.concat([test_df_cleaned, test_df['track_uri']],axis=1)
calibration, withheld = train_test_split(test_df_cleaned, test_size=0.8, random_state=209, stratify = test_df_cleaned['pid'])
withheld.drop_duplicates(subset ="track_uri",keep = False, inplace = True)

C:\Users\Royce\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [6]:
train.describe()

acousticness  danceability    duration_ms        energy  \
count  13562.000000  13562.000000   13562.000000  13562.000000   
mean       0.157796      0.651324  234039.366023      0.685388   
std        0.198003      0.148380   51493.366351      0.167506   
min        0.000006      0.144000   19133.000000      0.027900   
25%        0.020000      0.549000  202723.250000      0.574000   
50%        0.073450      0.658000  225991.500000      0.702000   
75%        0.222000      0.757000  256703.500000      0.813000   
max        0.987000      0.980000  826813.000000      0.996000   

       instrumentalness           key      liveness      loudness  \
count      13562.000000  13562.000000  13562.000000  13562.000000   
mean           0.012731      5.128300      0.186206     -6.434418   
std            0.076586      3.668483      0.144203      2.653691   
min            0.000000      0.000000      0.015700    -34.475000   
25%            0.000000      1.000000      0.092000     -7.703000   
50%            0.000000      5.000000      0.128000     -5.907000   
75%            0.000048      8.000000      0.249000     -4.574750   
max            0.987000     11.000000      1.000000     -0.698000   

               mode   speechiness         tempo  time_signature       valence  
count  13562.000000  13562.000000  13562.000000    13562.000000  13562.000000  
mean       0.647028      0.110930    122.022105        3.978985      0.553528  
std        0.477912      0.109549     28.255147        0.260324      0.226203  
min        0.000000      0.022500     34.717000        0.000000      0.034000  
25%        0.000000      0.038500     99.973250        4.000000      0.382000  
50%        1.000000      0.060500    120.076000        4.000000      0.559000  
75%        1.000000      0.141000    140.000000        4.000000      0.737750  
max        1.000000      0.956000    210.750000        5.000000      0.990000

### Dropping duplicates
In the baseline model, given that we are only looking at predicting songs based on their similarity to other tracks, we can drop duplicates of the same song from the training set. We do so below.

In [7]:
train.drop_duplicates(subset ="track_uri",keep = False, inplace = True) 
train.head()

acousticness  danceability  duration_ms  energy  instrumentalness  key  \
5        0.00563         0.800       159693   0.677           0.00409    0   
12       0.02940         0.758       222180   0.756           0.00000   10   
19       0.19600         0.855       238530   0.522           0.00000    3   
22       0.10700         0.703       214757   0.806           0.00000    2   
26       0.57700         0.670       130293   0.724           0.00000   11   

    liveness  loudness  mode  speechiness    tempo  time_signature  valence  \
5     0.0838    -4.023     1       0.0393  125.004               4    0.547   
12    0.0906    -5.059     0       0.1380  145.068               4    0.406   
19    0.1000    -5.540     1       0.2260  139.917               4    0.355   
22    0.1340    -6.415     1       0.1530   94.979               4    0.279   
26    0.7890    -4.141     1       0.3610  145.105               4    0.285   

                               track_uri  
5   spotify:track:5bcfWAHLoMfGBdbeyoMaH3  
12  spotify:track:1rZah1UGXvgiQCqLVlq4hS  
19  spotify:track:2okC0OWtgS86P2LC18IzHy  
22  spotify:track:2FdQ4hkbqZ1X930oxxgZZy  
26  spotify:track:1Wsbr1d2BouNGk2q92mIj7

In [8]:
train = train.set_index('track_uri') 

In [9]:
train.shape

(3098, 13)

### Fitting the training set to a Nearest Neighbors model

This leaves us with 3098 songs in our training set, which we then fit onto an unsupervised Nearest Neighbors learning model, where n_neighbors = 20 and cosine distance is used as a distance of measure. 

Here, we have set the neighbors search algorithm to auto, so that the algorithm attempts to determine the best approach from the training data across the options of BallTree, KDTree, and a brute-force algorithm.

In [10]:
# pivot ratings into song features
model_knn = NearestNeighbors(metric='cosine', algorithm='auto', n_neighbors=20, n_jobs=-1)# fit the dataset
model_knn.fit(train)

NearestNeighbors(algorithm='auto', leaf_size=30, metric='cosine',
         metric_params=None, n_jobs=-1, n_neighbors=20, p=2, radius=1.0)

### Creating a function to make recommendations

We then proceed to create a function that will take as inputs 1) the Nearest Neighbors model fitted on the training data, 2) a playlist id (to identify the songs in the test set), 3) the number of neighbors to select from and 4) number of recommended songs to predict.

This function will return a list of recommended songs.

In [11]:
def make_recommendation(model_knn, playlist_id, n_neighbors, n_recommendations):
    
    calibration_songs = calibration[calibration['pid']==playlist_id]
    calibration_songs_clean = calibration_songs.drop(columns=['pid', 'track_uri'])

    song_freq_dict = {}

    for index, song in calibration_songs_clean.iterrows():
        distances, indices = model_knn.kneighbors(song.values.reshape(1,-1), n_neighbors=n_neighbors)

        for index in indices[0]:
            if song_freq_dict.get(index) is None:
                song_freq_dict[index] = 1
            else:
                song_freq_dict[index] += 1

    k = Counter(song_freq_dict) 

    # Finding n highest values 
    top_songs = [i[0] for i in k.most_common(n_recommendations)]    

    rec_songs = train.iloc[top_songs].index

    return rec_songs

### Measuring success

For starters, we will use the R-precision score to measure how successful our song predictions are. Here, we define a function `r_precision`, which computes number of retrieved relevant tracks divided by the number of known relevant tracks (i.e., the number of withheld tracks). It takes as inputs a list of predicted songs and compares it against a list of the actual songs from the given playlist ("withheld songs").

In [12]:
#Function to calculate r_precision (https://recsys-challenge.spotify.com/rules)
#R-precision is the number of retrieved relevant tracks divided by the number of known relevant tracks (i.e., the number of withheld tracks) 

def r_precision(preds, known):
    for i in known:
        if i in preds:
            song = test_df[test_df['track_uri']==i]['track_name']
            print(f'{song} appeared in both our predicted playlist and the known list of songs.')
    score = np.sum(known.isin(preds))/known.shape[0]
    return score

### Running the baseline model on test data

We then run the following code to loop through all the unique playlists in the test set to predict songs based on a random subset of 20% of songs from the given test playlist (`calibration`). The predicted songs are then fed into the R-precision score function together with the remaining 80% of songs from the given test playlist (`withheld`).

For testing purposes, we print out the actual track names of the songs being predicted and the withheld songs, so that we can get a qualitative understanding of the songs.

In [13]:
n_neighbors = [10, 50, 100]
n_recommendations = [10, 50, 100]

r_precision_scores = []
overall_rps_list = []
neighbors = []
recommendations = []

for x in n_neighbors: 
    for y in n_recommendations:
        #Loop through all unique playlists in test set to identify predicted songs
        for index, pid in enumerate(withheld['pid'].drop_duplicates()): 
            print (index, pid)
            pred_songs = make_recommendation(model_knn, pid, x, y)
            validation_set = withheld[withheld.pid == pid].track_uri
            print("Predicted songs\n", train_df[train_df['track_uri'].isin(pred_songs)]['track_name'])
            print("Known songs\n", test_df[test_df['track_uri'].isin(validation_set)]['track_name'])
            rps = r_precision(list(pred_songs), validation_set)
            r_precision_scores.append(rps)
        avg_rp = np.mean(r_precision_scores)
        neighbors.append(x)
        recommendations.append(y)
        overall_rps_list.append(avg_rp)
        
        #dict_rps["No. of neighbors: "+str(x)+", "+"No. of predictions per playlist: " + str(y)] = avg_rp
        print(f'For neighbours {x} and recommendations {y}: The averaged R precision score is {avg_rp}')

0 273004
Predicted songs
 1290                            Everything Is Embarrassing
3337                                           4r Da Squaw
5110                                    Can't Make This Up
5911                                              Curtains
6672                                      He Said She Said
10496                                  Let Me Take You Out
10761    My Boo (feat. Vince Staples, Kučka, Ngaiire & ...
12096                                        When it Rains
12198                               Sleeping With A Friend
13438                                              Tonight
Name: track_name, dtype: object
Known songs
 1358                                               Poison
2254                                       Ain't My Fault
2583                                            Confident
4791                                               Poison
4792                                         Let's Groove
4793                                             

Predicted songs
 496                    Mind Playing Tricks on Me
3117                          Cats In The Cradle
3349                                 Veridis Quo
3796                    Step In the Name of Love
4149                                    Blue Sky
5127                                   Spotlight
6907                      Do You Wanna Get High?
7890                                   Confident
8407    Sherane a.k.a Master Splinter’s Daughter
9716                            American Soldier
Name: track_name, dtype: object
Known songs
 4060                                             Even Flow
4961                                    When I Come Around
5561                                            Maggie May
6373                          Stuck In The Middle With You
6382                              Brown Sugar - Remastered
6383     Long Cool Woman (In A Black Dress) - 1999 Rema...
6386                      I Heard It Through The Grapevine
6390                               

Predicted songs
 3113                            Mama, I'm Coming Home
5358                                       Come Clean
5390                                           Say Ok
6227                Deep Inside of You - 2008 Version
10511    Going Back To Cali - 2014 Remastered Version
10739                                         Luh You
12064                           She Likes the Beatles
12867                                 Ain't Your Mama
13190                              I'm In Miami Bitch
13334                                         Fifteen
Name: track_name, dtype: object
Known songs
 1151                                            Doe-Active
1154                                          Shabba REMIX
1156                                      Yamborghini High
1157                                       Telephone Calls
1159                                                   M'$
1163                                          Frozen Water
1164                                        

Predicted songs
 530                                  Thuggish Ruggish Bone
795          Beautiful Liar - Main Version / Album Version
2885                  No Faith in Brooklyn (feat. Jhameel)
5945                                          Bring Em Out
6317                Better Days (And The Bottom Drops Out)
8306                                                Dirrty
10761    My Boo (feat. Vince Staples, Kučka, Ngaiire & ...
10925              Obsession (feat. Jon Bellion) - RAC Mix
12378                                        Back To Sleep
13120                                         Up All Night
Name: track_name, dtype: object
Known songs
 2808     It's Goin' Down (feat. Nitti) - Feat. Nitti Ex...
2993                     Dreaming - The Chainsmokers Remix
6518                                             Get Crazy
6519                              FUCKING BEST SONG EVERRR
6522          I Love It When You Cry (Moxoki) - Radio Edit
6548                                           Do My 

Predicted songs
 2386                                Last Train to London
3103           Should I Stay or Should I Go - Remastered
4353                     Don't Let The Sun Go Down On Me
4483                                            Soulmate
5028                                      You're So Vain
5491                                              Winter
8474                                                2100
8906    Some Kind Of Wonderful - Digitally Remastered 99
8934          Gonna Make You Sweat (Everybody Dance Now)
9314                                       I Know Places
Name: track_name, dtype: object
Known songs
 4008                                    Friday I'm In Love
5554                                     Boogie Wonderland
5581                                             The Joker
5810                                                Africa
6371                                             The Joker
6379                                    I Shot The Sheriff
6478          

...

Predicted songs
 145                         LoveHate Thing - feat. Sam Dew
202                                           Shake Ya Ass
258                                            Sex Therapy
539                                          Ms. Fat Booty
571                                             C.R.E.A.M.
840                                          Lejos De Aquí
1131                                               Mercy.1
1425                           Open Season - Gryffin Remix
1457                                      We Got The Party
1881                                               My Body
1903                                       Time Well Spent
1945                                           Dayum, Baby
2601                                      Freak On a Leash
2644                                            South Side
2727                                             Bounce It
2732                                                Swerve
2825                                   

Predicted songs
 107                                              Do You...
233                                Slow Down - 12" Version
479                                                     Ha
571                                             C.R.E.A.M.
841                                                   6 AM
877                                                   Army
1301                        Bad (feat. Vassy) - Radio Edit
1311                            Another Love - Zwette Edit
1389         I'd Love To Change The World - Matstubs Remix
1457                                      We Got The Party
1508                                        Start All Over
1509                                            I Miss You
1541                                               We Rock
1691                                                   Fly
1719               Sober Saturday Night (feat. Vince Gill)
2158                                 Kick It In The Sticks
3358                                   

Predicted songs
 206                                     Aston Martin Music
350                                             Obstacle 1
485            Chickenhead (feat. La Chat & Three 6 Mafia)
495                    Int'l Players Anthem (I Choose You)
677                                                   Donk
728                                    Peanut Butter Jelly
738                       Home - Fedde Le Grand Radio Edit
838                                          Body Language
1104                                              Research
1288                Five More Hours - Deorro x Chris Brown
1302                                  Heroes (we could be)
1375                        The Nights - Felix Jaehn Remix
1493                                           Stacy's Mom
1551                    Strut - From "The Cheetah Girls 2"
1792                                     That Should Be Me
1865                                              Be Still
1877                                   

Predicted songs
 19                          Bake Sale (feat. Travis Scott)
345                                    Gold On The Ceiling
485            Chickenhead (feat. La Chat & Three 6 Mafia)
495                    Int'l Players Anthem (I Choose You)
527                                       Shimmy Shimmy Ya
757                                             Fine By Me
763                                                 Hollow
812                                       Some Type of Way
1250                            Save the World - Radio Mix
1255                                      Something Better
1288                Five More Hours - Deorro x Chris Brown
1302                                  Heroes (we could be)
1375                        The Nights - Felix Jaehn Remix
1383                                         Pure Grinding
1416                                     Perfect Strangers
1551                    Strut - From "The Cheetah Girls 2"
1693                                  B

Predicted songs
 12                                      King Of Everything
45                                                     WOA
98                            Pull Up (feat. Lil Uzi Vert)
165                                 Neighbors Know My Name
206                                     Aston Martin Music
368                                              Lazaretto
591                                             Tambourine
736                                               Hangover
737                     Pumpin Blood - The Jane Doze Remix
738                       Home - Fedde Le Grand Radio Edit
1084                                            Basketball
1367                                    Whole Lotta Lovin'
1435            Run Up (feat. PARTYNEXTDOOR & Nicki Minaj)
1482               Dirt Off Your Shoulder / Lying From You
1839                              Every Rose Has Its Thorn
1892                                           Kiss a Girl
1967                                   

### Measuring success

To measure success for the baseline model, we compute the mean of the R-precision scores across all the playlists in the test set, across different values for the parameters of number of neighbors and number of predictions.

In [14]:
neighbors
recommendations
overall_rps_list

[0.0025233457019171305,
 0.005492765145415483,
 0.008522834463805801,
 0.0065770748274461876,
 0.006709751653026114,
 0.007639247400051365,
 0.006718263252368517,
 0.006487092532047375,
 0.006978321806857027]

In [15]:
dfObj = pd.DataFrame({'No. of neighbors': neighbors, 'No. of predictions': recommendations, 'R-precision score': overall_rps_list})
dfObj

No. of neighbors  No. of predictions  R-precision score
0                10                  10           0.002523
1                10                  50           0.005493
2                10                 100           0.008523
3                50                  10           0.006577
4                50                  50           0.006710
5                50                 100           0.007639
6               100                  10           0.006718
7               100                  50           0.006487
8               100                 100           0.006978

In [16]:
print('Highest Avg. R-Precision Score: ', max(dfObj['R-precision score']))

Highest Avg. R-Precision Score:  0.008522834463805801


The highest value returned across the combinations of parameters was 0.0085, which implies that on average, out of all the withheld songs in the test playlists, we only manage to predict 0.85% of them using our model. This is extremely low - however, as a baseline model, this model gives us a sense of the challenges involved in predicting songs. 

### Challenges and next steps

One of the significant challenges that we have identified could be the fact that the withheld songs in the test data set are not in our original training set. Hence, logically, the model trained on songs in the training set would not be able to return predicted songs that would match 1-to-1 with the withheld songs.

To validate this hypothesis, we ran a quick check on the intersection of songs between both sets, and as expected, only 635 songs in the withheld list of songs, out of a total of 2991 unique songs, appear in the training set.

Going ahead, for the next milestone, this will mean having to expand the training set to increase the overlap in songs between the two sets.

In [17]:
def intersection(lst1, lst2): 
    lst3 = [value for value in lst1 if value in lst2] 
    return lst3 
  
print (len(intersection(list(withheld.track_uri), list(train.index))))
print (len(list(withheld.track_uri)))

635
2991
